In [1]:
# import stuff based on the provided assignments

import numpy as np
import datetime as dt
import matplotlib.pyplot as plt
from scipy.stats import norm, lognorm
import pandas as pd
from pyfinance.options import BSM
from mpl_toolkits.mplot3d import Axes3D
from datar import f
from datar.dplyr import mutate, filter, if_else, pull, group_by, select

[2021-11-29 20:46:35][datar][WARNING] Builtin name "filter" has been overriden by datar.


In [2]:
"""function for testing frequencies and different strikes for all worksheets"""

def read_data(xls,worksheet):
    return pd.read_excel(xls, worksheet)
    

def format_data(df,expiry):
    """Convert into correct format"""
    df.rename(dict(zip(np.append(np.array(df.columns[0]), df.columns[-3:]), ['T', 'S', 'r', 'date'])), axis='columns', inplace=True)
    df = df.melt(id_vars=['T', 'r', 'S', 'date'], var_name="E").dropna()
    df['date'] = pd.to_datetime(df['date'], dayfirst=True)
    df['name'] = df['E'].astype('str') + '-' + expiry
    
    df.rename({'value':'Cobs'}, axis='columns', inplace=True)
    df = df  >> mutate(r = f.r/100, Mat = f.T, T = f.T/252, S = f.S/1000, E = f.E/1000, Cobs = f.Cobs/1000)
    df['Mat'] = df['Mat'].astype('int')
    
    return df
    
def calculate_bs_greeks(row):
    """Calculate IV and using that as volatility find delta and vega"""
    S=row['S']
    E=row['E']
    r=row['r']
    T=row['T']
    Cobs=row['Cobs']
    
    starting_vol = .2
    bsm = BSM(S, E, T, r, starting_vol)
    iv = bsm.implied_vol(Cobs, precision=1.0e-3)
    
    bsm_iv = BSM(S, E, T, r, iv)
    
    delta = bsm_iv.delta()
    vega = bsm_iv.vega()
    
    return iv, delta, vega
    
def simulate_portfolio(df_data, strike, frequency):
    """
    Simulate portfolio of long 1 call, short delta*stock
    with given strike and rebalancing frequency.
    Returns array of errors, average stock price for data and how many observations there were
    """
    n = 0
    p_o = df_data[df_data['E'] == strike].iloc[0]['Cobs']
    p_s = {
        'price':df_data[df_data['E'] == strike].iloc[0]['S'],
        'delta':df_data[df_data['E'] == strike].iloc[0]['delta']
    }
    error_arr = np.array([])

    for index, data in df_data[df_data['E'] == strike].reset_index(drop=True).iterrows():
        T,r,S,date,E,cobs,name,mat,iv,delta,vega = data

        if n == frequency:
            p_o, p_s, error = hedge(p_o, p_s, cobs, S, delta)
            error_arr = np.append(error_arr, error)
            n = 0
        n += 1
    return error_arr,df_data[df_data['E'] == strike]['S'].mean(),df_data[df_data['E'] == strike]['S'].median(),len(df_data[df_data['E'] == strike])

def hedge(p_o, p_s, cobs, S, delta):
    option_gain = cobs - p_o
    stock_gain = -delta * (S - p_s['price'])
    error = option_gain + stock_gain
    
    return cobs, {'price':S, 'delta':delta}, error**2

def test_sheet(excel, sheet_name, sheetnr):
    day = str(sheet_name[3:5])
    month = str(sheet_name[5:7])
    year = str(sheet_name[7:11])
    expiry=year+month+day

    
    df = format_data(read_data(xls, sheet_name), expiry)
    greeks = df.apply(calculate_bs_greeks, axis=1, result_type='expand')
    df[['iv', 'delta', 'vega']] = greeks
    df = df >> filter(0 < f.iv < 0.6)
    
    min_freq = 1
    max_freq = 6
    
    obs = {
    'strike':[],
    'avg_price':[],
    'median_price':[],
    'freq':[],
    'mse':[],
    'n':[],
    'sheet':[]
    }
    
    for strike in df['E'].unique():
        for freq in range(min_freq,max_freq):
            error, average_price, median_price, count = simulate_portfolio(df, strike, freq)
            obs['strike'].append(strike)
            obs['avg_price'].append(average_price)
            obs['median_price'].append(median_price)
            obs['freq'].append(freq)
            obs['mse'].append(error.mean())
            obs['n'].append(count)
            obs['sheet'].append(sheetnr)
    return df, obs


In [3]:
xls = pd.ExcelFile('data/isx2010C.xls')
sheets = xls.sheet_names
sheets

sheet_order = [0,1,11,10,9,8,7,6,5,4,3,2]

all_obs = []
all_sheets = []

for i in sheet_order:
    df, obs = test_sheet(xls, sheets[i], i)
    all_obs.append(obs)
    all_sheets.append(df)

all_data = pd.concat(all_sheets)

/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance/options.py:242: RuntimeWarning: divide by zero encountered in double_scalars
  vol = vol + diff / opt.vega()
/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance/options.py:149: RuntimeWarning: invalid value encountered in double_scalars
  self.d1 = (
/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance/options.py:151: RuntimeWarning: overflow encountered in double_scalars
  + (self.r + 0.5 * self.sigma ** 2) * self.T
/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance/options.py:242: RuntimeWarning: divide by zero encountered in double_scalars
  vol = vol + diff / opt.vega()
/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance/options.py:149: RuntimeWarning: invalid value encountered in double_scalars
  self.d1 = (
/home/juuso/Documents/school/finaeng1/venv/lib/python3.9/site-packages/pyfinance

In [45]:
"""
Delta vega -hedging:
- Choose option
- Iterate over dates of that option
- For n interval, rehedge options position by:
    - Buying option with same strike and longer expiry
        - For given date and given strike, choose some other option
    - buying stock at that time

"""
def find_vega_hedges(data, date, option_mat):
    ok_hedges = data[(data['date'] == date) & (data['Mat'] > int(option_mat))]
    if len(ok_hedges) > 0:
        return 1
    return 0




# all unique options
all_options = all_data['name'].unique()
fully_hedgeable = []
for option in all_options:

    days_hedged = 0
    # data for the chosen option that will be hedged
    initial_option_data = all_data[all_data['name'] == option]
    option_E = initial_option_data['E'].unique()[0]
    
    # options with same strike but not same
    available_hedges = all_data[(all_data['E'] == option_E) & (all_data['name'] != option)]
    
    # loop over days for the option
    for index, row in initial_option_data.iterrows():
        T,r,S,date,E,cobs,name, mat,iv,delta,vega = row

        has_hedge = find_vega_hedges(available_hedges, date, mat)
        
        days_hedged += has_hedge
    
    if days_hedged == len(initial_option_data):
        
        fully_hedgeable.append(option)
        

|    |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |   delta |      vega |
|---:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|--------:|----------:|
| 20 | 0.515873 | 0.0011 | 0.49134 | 2009-09-21 00:00:00 | 0.34 | 0.1525 | 340-20100319 |   130 | 0.285109 | 0.97149 | 0.0230171 |
|    |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|---:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 21 | 0.511905 | 0.0011 | 0.49435 | 2009-09-22 00:00:00 | 0.34 | 0.1554 | 340-20100319 |   129 | 0.286163 | 0.973398 | 0.0217747 |
|    |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |     vega |
|---:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-----

|    |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|---:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 24 | 0.261905 | 0.0004 | 0.50879 | 2009-11-20 00:00:00 | 0.34 | 0.1695 | 340-20100219 |    66 | 0.415432 | 0.977398 | 0.0139809 |
| 64 | 0.34127  | 0.0004 | 0.50879 | 2009-11-20 00:00:00 | 0.34 | 0.1696 | 340-20100319 |    86 | 0.368236 | 0.976261 | 0.0166329 |
|    |        T |      r |     S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|---:|---------:|-------:|------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 25 | 0.257937 | 0.0004 | 0.516 | 2009-11-23 00:00:00 | 0.34 | 0.1762 | 340-20100219 |    65 | 0.400599 | 0.984326 | 0.0103061 |
| 65 | 0.337302 | 0.0004 | 0.516 | 2009-11-23 00:00:00 | 0.34 | 0.1762 | 340-20100

|     |        T |      r |       S | date                |    E |    Cobs | name         |   Mat |       iv |    delta |      vega |
|----:|---------:|-------:|--------:|:--------------------|-----:|--------:|:-------------|------:|---------:|---------:|----------:|
| 370 | 0.31746  | 0.0007 | 0.48515 | 2009-11-02 00:00:00 | 0.36 | 0.1262  | 360-20100219 |    80 | 0.302739 | 0.966799 | 0.0202248 |
| 650 | 0.396825 | 0.0007 | 0.48515 | 2009-11-02 00:00:00 | 0.36 | 0.12695 | 360-20100319 |   100 | 0.295952 | 0.954966 | 0.0289858 |
|     |        T |      r |      S | date                |    E |    Cobs | name         |   Mat |       iv |    delta |      vega |
|----:|---------:|-------:|-------:|:--------------------|-----:|--------:|:-------------|------:|---------:|---------:|----------:|
| 371 | 0.313492 | 0.0007 | 0.4849 | 2009-11-03 00:00:00 | 0.36 | 0.1261  | 360-20100219 |    79 | 0.310452 | 0.964198 | 0.0213718 |
| 651 | 0.392857 | 0.0007 | 0.4849 | 2009-11-03 00:00:00 | 0.36 |

|     |        T |      r |       S | date                |     E |    Cobs | name         |   Mat |       iv |    delta |      vega |
|----:|---------:|-------:|--------:|:--------------------|------:|--------:|:-------------|------:|---------:|---------:|----------:|
| 675 | 0.178571 | 0.0004 | 0.51394 | 2009-12-21 00:00:00 | 0.375 | 0.13925 | 375-20100219 |    45 | 0.378898 | 0.979768 | 0.0106188 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 1220 | 0.515873 | 0.0011 | 0.49134 | 2009-09-21 00:00:00 | 0.38 | 0.1149 | 380-20100319 |   130 | 0.277184 | 0.918208 | 0.0533492 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |      iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|

|     |        T |      r |     S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|----:|---------:|-------:|------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 925 | 0.257937 | 0.0004 | 0.516 | 2009-11-23 00:00:00 | 0.39 | 0.1264 | 390-20100219 |    65 | 0.286453 | 0.977131 | 0.0142112 |
|     |        T |      r |      S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|----:|---------:|-------:|-------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 926 | 0.253968 | 0.0004 | 0.5158 | 2009-11-24 00:00:00 | 0.39 |  0.126 | 390-20100219 |    64 | 0.277723 | 0.980691 | 0.0122156 |
|     |    T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |     vega |
|----:|-----:|-------:|--------:|:--------------------|-----:|-------:|:-----------

...

| 6173 | 0.22619 | 0.0016 | 0.51465 | 2010-09-30 00:00:00 | 0.51 | 0.02185 | 510-20101217 |    57 | 0.199044 | 0.558448 | 0.0965972 |
|      |        T |      r |       S | date                |    E |    Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|--------:|:-------------|------:|---------:|---------:|----------:|
| 6174 | 0.222222 | 0.0016 | 0.51722 | 2010-10-01 00:00:00 | 0.51 | 0.02315 | 510-20101217 |    56 | 0.199179 | 0.579436 | 0.0953354 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 6175 | 0.218254 | 0.0016 | 0.51331 | 2010-10-04 00:00:00 | 0.51 | 0.0212 | 510-20101217 |    55 | 0.203617 | 0.547458 | 0.0949912 |
|      |        T |      r |       S | date                

|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 6537 | 0.194444 | 0.0013 | 0.52854 | 2010-10-12 00:00:00 | 0.52 | 0.0223 | 520-20101217 |    49 | 0.191335 | 0.594158 | 0.0903773 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 6538 | 0.190476 | 0.0013 | 0.53186 | 2010-10-13 00:00:00 | 0.52 | 0.0247 | 520-20101217 |    48 | 0.197934 | 0.620622 | 0.0883378 |
|      |        T |      r |       S | date                |    E |    Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-

| 6899 | 0.170635 | 0.0014 | 0.53244 | 2010-10-20 00:00:00 | 0.53 | 0.0166 | 530-20101217 |    43 | 0.174632 | 0.54104 | 0.0872788 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|----------:|
| 6900 | 0.166667 | 0.0014 | 0.53346 | 2010-10-21 00:00:00 | 0.53 | 0.0148 | 530-20101217 |    42 | 0.149349 | 0.556079 | 0.0860235 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |    delta |     vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|---------:|---------:|
| 6901 | 0.162698 | 0.0014 | 0.53419 | 2010-10-22 00:00:00 | 0.53 | 0.0167 | 530-20101217 |    41 | 0.168745 | 0.560829 | 0.084959 |
|      |       T |      r |       S | date                |    E |

| 7245 | 0.210317 | 0.0016 | 0.52447 | 2010-10-06 00:00:00 | 0.54 | 0.0101 | 540-20101217 |    53 | 0.175902 | 0.375535 | 0.0912464 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |       iv |   delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|---------:|--------:|----------:|
| 7246 | 0.206349 | 0.0016 | 0.52339 | 2010-10-07 00:00:00 | 0.54 | 0.0091 | 540-20101217 |    52 | 0.173957 | 0.36254 | 0.0891622 |
|      |        T |      r |       S | date                |    E |   Cobs | name         |   Mat |      iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-----:|-------:|:-------------|------:|--------:|---------:|----------:|
| 7247 | 0.202381 | 0.0013 | 0.52627 | 2010-10-08 00:00:00 | 0.54 | 0.0098 | 540-20101217 |    51 | 0.16717 | 0.381569 | 0.0902573 |
|      |        T |      r |       S | date                |    E | 

|      |        T |      r |       S | date                |     E |   Cobs | name         |   Mat |       iv |   delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|------:|-------:|:-------------|------:|---------:|--------:|----------:|
| 7798 | 0.134921 | 0.0013 | 0.53754 | 2010-11-02 00:00:00 | 0.555 |  0.006 | 555-20101217 |    34 | 0.161436 | 0.30627 | 0.0692889 |
|      |        T |      r |       S | date                |     E |   Cobs | name         |   Mat |       iv |    delta |     vega |
|-----:|---------:|-------:|--------:|:--------------------|------:|-------:|:-------------|------:|---------:|---------:|---------:|
| 7799 | 0.130952 | 0.0013 | 0.54021 | 2010-11-03 00:00:00 | 0.555 | 0.0057 | 555-20101217 |    33 | 0.147047 | 0.316401 | 0.069576 |
|      |        T |      r |       S | date                |     E |   Cobs | name         |   Mat |       iv |    delta |      vega |
|-----:|---------:|-------:|--------:|:--------------------|-

In [ ]:

def delta_vega_hedge(data, date, maturity, cobs, delta, vega, stock, init=False):
    """
    short option with shorter maturity
    long option with same strike and longer maturity equal to amount of vega(short)/vega(long)
    long stock for delta(short) - (vega(short)/vega(long))*delta(long)
    
    hedge error is new portfolio value - previous portfolio value
    """
    if not init:
        # profit on short is (-price(t) - (-price(t-1))) = -price(t) + price(t-1)
        short_option_profit = -cobs - portfolio['portfolio_option_price']

        # profit on hedge option is amount*price(t) - amount*price(t-1) = amount (price(t) - price(t-1))
        old_hedge_current_price = data[(data['date'] == date) & (data['name'] == portfolio['hedge_option_name'])]['Cobs']
        hedge_option_profit = portfolio['hedge_option_amount']* (old_hedge_current_price - portfolio['hedge_option_price'])

        # stock profit = amount * (price(t) - price(t-1))
        stock_profit = portfolio['hedge_stock_amount'] * (stock - portfolio['hedge_stock_price'])
        
        hedge_error = short_option_profit - (hedge_option_profit + stock_profit)
        
    
    try:
        ok_hedges = data[(data['date'] == date) & (data['Mat'] > int(maturity))]
        selected_hedge = ok_hedges[ok_hedges['Mat'] == ok_hedges['Mat'].max()]


        hedge_option_name, hedge_option_price, hedge_option_delta, hedge_option_vega = selected_hedge[['name', 'Cobs', 'delta','vega']].values[0]

        hedge_option_amount = -vega/hedge_option_vega
        hedge_stock_amount = -delta - hedge_option_amount * hedge_option_delta
    except BaseException as err:
        print(f"Unexpected {err=}, {type(err)=}")
        try:
            ok_hedges = data[(data['date'] == date) & (data['Mat'] > int(maturity))]
            selected_hedge = ok_hedges[ok_hedges['Mat'] == ok_hedges['Mat'].min()]


            hedge_option_name, hedge_option_price, hedge_option_delta, hedge_option_vega = selected_hedge[['name', 'Cobs', 'delta','vega']].values[0]

            hedge_option_amount = -vega/hedge_option_vega
            hedge_stock_amount = -delta - hedge_option_amount * hedge_option_delta
        except:
            raise ValueError('Failed all options')
            
    
    
    new_portfolio = {
        'portfolio_option_price':-cobs,
        'hedge_option_name':hedge_option_name,
        'hedge_option_price':hedge_option_price,
        'hedge_option_amount':hedge_option_amount,
        'hedge_stock_price':stock,
        'hedge_stock_amount':hedge_stock_amount
    }
    
    if init:
        return new_portfolio
    
    #print(hedge_error)
    
    return hedge_error, new_portfolio

  
    
frequency = 2


for option in fully_hedgeable:
    try:
        n = 0
        total_error = np.array([])

        days_hedged = 0
        # data for the chosen option that will be hedged
        initial_option_data = all_data[all_data['name'] == option]
        option_E = initial_option_data['E'].unique()[0]

        # options with same strike but not same
        available_hedges = all_data[(all_data['E'] == option_E) & (all_data['name'] != option)]

        first_row = all_data[all_data['name'] == option].iloc[0]
        portfolio = delta_vega_hedge(available_hedges, first_row['date'], first_row['Mat'], first_row['Cobs'], first_row['delta'], first_row['vega'], first_row['S'], init=True)

        # loop over days for the optio
        for index, row in initial_option_data.iterrows():
            T,r,S,date,E,cobs,name, mat,iv,delta,vega = row

            if n == frequency:
                error_term, portfolio = delta_vega_hedge(available_hedges, date, mat, cobs, delta, vega, S)
                total_error = np.append(total_error, error_term)
                n = 0
            n += 1
    except BaseException as err:
        # some scenarios have vega = 0 for hedge option
        print(f"Unexpected {err=}, {type(err)=}")

Unexpected err=ZeroDivisionError('float division by zero'), type(err)=<class 'ZeroDivisionError'>
Failed all options
Unexpected err=ValueError('Failed all options'), type(err)=<class 'ValueError'>
Unexpected err=ZeroDivisionError('float division by zero'), type(err)=<class 'ZeroDivisionError'>
Failed all options
Unexpected err=ValueError('Failed all options'), type(err)=<class 'ValueError'>
Unexpected err=ZeroDivisionError('float division by zero'), type(err)=<class 'ZeroDivisionError'>
Failed all options
Unexpected err=ValueError('Failed all options'), type(err)=<class 'ValueError'>
